In [ ]:
import pandas as pd

In [ ]:
data_article = pd.read_parquet("Articles//use//articles.parquet")
data_article['type'] = 'article'
data_event = pd.read_parquet("Articles//use//events.parquet")
data_event['type'] = 'event'
data_event['date'] = data_event['eventDate']
data_event_merge = data_event[['uri','title_txt','summary_txt','type','date']]
data_event_merge = data_event_merge.rename(columns={"title_txt":"title", "summary_txt":"body"})
data_news = pd.concat([data_article[['uri', 'title', 'body','type','date']],data_event_merge[['uri','title','body','type','date']]], ignore_index=True)
data_news

uri                                              title  \
0      8571515568  Currys scraps advice telling customers use a s...   
1      8571512101                                      Weekly review   
2      8571511956  Chinese Cars Account For 76% Global EV and PHE...   
3      8571511074  TESLA I Its not only EV Cars. Elon Musk predic...   
4      8571511614  UK train passengers face "further misery" as f...   
..            ...                                                ...   
348  eng-10368906  BP to slash renewables investment and ramp up ...   
349  eng-10360298  "Remove Trade Tariffs for Nigeria": FG appeals...   
350  eng-10354241  Clean energy contributed 10% to China's GDP in...   
351  eng-10327507  Data science and AI: The twin engines powering...   
352  eng-10320057  Trump Suspends $5 Billion Electric Vehicle Cha...   

                                                  body     type        date  
0    Electrical retailer Currys have scrapped advic...  article  2025-03-02  
1    Education publisher Pearson on Friday said ann...  article  2025-03-02  
2    Electric carsare demonstrating more market pen...  article  2025-03-02  
3    This is not a short-term trade as you know fro...  article  2025-03-02  
4    (Alliance News) - Train fares in England and W...  article  2025-03-02  
..                                                 ...      ...         ...  
348  Some shareholders and environmental groups hav...    event  2025-02-24  
349  CHECK OUT: Education is Your Right! Don't Let ...    event  2025-02-20  
350  Study found electric vehicles and batteries ad...    event  2025-02-19  
351  Climate change faces its critical juncture tod...    event  2025-02-10  
352  President Donald Trump's administration halted...    event  2025-02-07  

[353 rows x 5 columns]

In [ ]:
data_news['txt'] = data_news['title'] + ". " + data_news["body"]
data_news

uri                                              title  \
0      8571515568  Currys scraps advice telling customers use a s...   
1      8571512101                                      Weekly review   
2      8571511956  Chinese Cars Account For 76% Global EV and PHE...   
3      8571511074  TESLA I Its not only EV Cars. Elon Musk predic...   
4      8571511614  UK train passengers face "further misery" as f...   
..            ...                                                ...   
348  eng-10368906  BP to slash renewables investment and ramp up ...   
349  eng-10360298  "Remove Trade Tariffs for Nigeria": FG appeals...   
350  eng-10354241  Clean energy contributed 10% to China's GDP in...   
351  eng-10327507  Data science and AI: The twin engines powering...   
352  eng-10320057  Trump Suspends $5 Billion Electric Vehicle Cha...   

                                                  body     type        date  \
0    Electrical retailer Currys have scrapped advic...  article  2025-03-02   
1    Education publisher Pearson on Friday said ann...  article  2025-03-02   
2    Electric carsare demonstrating more market pen...  article  2025-03-02   
3    This is not a short-term trade as you know fro...  article  2025-03-02   
4    (Alliance News) - Train fares in England and W...  article  2025-03-02   
..                                                 ...      ...         ...   
348  Some shareholders and environmental groups hav...    event  2025-02-24   
349  CHECK OUT: Education is Your Right! Don't Let ...    event  2025-02-20   
350  Study found electric vehicles and batteries ad...    event  2025-02-19   
351  Climate change faces its critical juncture tod...    event  2025-02-10   
352  President Donald Trump's administration halted...    event  2025-02-07   

                                                   txt  
0    Currys scraps advice telling customers use a s...  
1    Weekly review. Education publisher Pearson on ...  
2    Chinese Cars Account For 76% Global EV and PHE...  
3    TESLA I Its not only EV Cars. Elon Musk predic...  
4    UK train passengers face "further misery" as f...  
..                                                 ...  
348  BP to slash renewables investment and ramp up ...  
349  "Remove Trade Tariffs for Nigeria": FG appeals...  
350  Clean energy contributed 10% to China's GDP in...  
351  Data science and AI: The twin engines powering...  
352  Trump Suspends $5 Billion Electric Vehicle Cha...  

[353 rows x 6 columns]

In [ ]:
data_news.to_parquet("Data_use//unjoined_parquet//news.parquet")

In [ ]:
OPENAI_API_KEY = ''

import os

os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY

In [ ]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(
    model="gpt-4o",
    temperature=0,
)

In [ ]:
import time
import tqdm

data_news_use = data_news

responses = [None] * len(data_news_use)  # Preallocate list to keep order
queries = [None] * len(data_news_use)

def process_row(index, input_data):
    query = f"""
    you are helpful assistant that recognize entity inside article with NER.
    Identify Entities in article below and then include it into a group.
    the available group :
    Person, Country, Location, Organization, World Organization, Environment Pollutant, Renewable Energy, Electric Vehicle, Green Technology, Brand.
    If the entity is not belongs into those group, skip it.
    answer response in format strict to this example, without any addition
    Example response:
    [
        {{"word": "Jensen Huang", "entity": "Person"}},
        {{"word": "electric car", "entity": "Electric Vehicle"}},
        {{"word": "Germany", "entity": "Country"}},
        {{"word": "Munich", "entity": "Location"}}
    ]
    article :
    {input_data['txt']}
    """
    response = llm.invoke(query)
    return index, query, response  # Return the index to maintain order

requests_processed = 0  # Counter to track the number of requests processed

with tqdm.tqdm(total=len(data_news_use), desc="Processing") as pbar:
    for i, row in data_news_use.iterrows():
        index, query, response = process_row(i, row)
        queries[index] = query  # Store at correct index
        responses[index] = response
        requests_processed += 1

        # Introduce 1-minute delay after every 10 requests
        if requests_processed % 10 == 0:
            print("Processed 10 requests, waiting for 1 minute...")
            time.sleep(60)  # Delay for 1 minute

        pbar.update(1)

Processing:   3%|▎         | 9/353 [01:19<35:33,  6.20s/it]  

Processed 10 requests, waiting for 1 minute...


Processing:   5%|▌         | 19/353 [03:28<42:58,  7.72s/it]  

Processed 10 requests, waiting for 1 minute...


Processing:   8%|▊         | 29/353 [06:06<57:04, 10.57s/it]  

...

Processing:  96%|█████████▌| 339/353 [1:08:41<00:58,  4.15s/it]

Processed 10 requests, waiting for 1 minute...


Processing:  99%|█████████▉| 349/353 [1:10:11<00:14,  3.51s/it]

Processed 10 requests, waiting for 1 minute...


Processing: 100%|██████████| 353/353 [1:11:22<00:00, 12.13s/it]


In [ ]:
print(responses[77].content)

```json
[
    {"word": "Mitsubishi Heavy Industries, Ltd.", "entity": "Organization"},
    {"word": "MarketBeat", "entity": "Organization"},
    {"word": "Wall Street", "entity": "Location"},
    {"word": "renewable energy", "entity": "Renewable Energy"}
]
```


In [ ]:
print(responses[0].content.replace("```json","").replace("```",""))


[
    {"word": "Currys", "entity": "Brand"},
    {"word": "MailOnline", "entity": "Organization"},
    {"word": "Jessica Watson", "entity": "Person"},
    {"word": "Gloriah", "entity": "Brand"},
    {"word": "Holly Jackson", "entity": "Person"},
    {"word": "SheSpot", "entity": "Brand"}
]



In [ ]:
print(queries[0])


    you are helpful assistant that recognize entity inside article with NER.
    Identify Entities in article below and then include it into a group.
    the available group : 
    Person, Country, Location, Organization, World Organization, Environment Pollutant, Renewable Energy, Electric Vehicle, Green Technology, Brand. 
    If the entity is not belongs into those group, skip it.
    answer response in format strict to this example, without any text or other addition 
    Example response:
    [
        {"word": "Jensen Huang", "entity": "Person"},
        {"word": "electric car", "entity": "Electric Vehicle"},
        {"word": "Germany", "entity": "Country"},
        {"word": "Munich", "entity": "Location"}
    ]
    article :
    Currys scraps advice telling customers use a sex toy on their COMMUTE. Electrical retailer Currys have scrapped advice to customers to use a sex toy on their commute after a warning from police that doing so could be illegal.

The high street giant this

In [ ]:
import ast
response_parsed = []

for resp in responses:
    response_parsed.append(ast.literal_eval(resp.content.replace("```json","").replace("```","")))

response_parsed[7]

[{'word': 'Volvo', 'entity': 'Brand'},
 {'word': 'ES90', 'entity': 'Electric Vehicle'},
 {'word': 'Swedish', 'entity': 'Country'},
 {'word': 'WLTP', 'entity': 'World Organization'},
 {'word': 'Indian', 'entity': 'Country'}]

In [ ]:
data_news_use['response_llm'] = response_parsed
data_news_use

uri                                              title  \
0      8571515568  Currys scraps advice telling customers use a s...   
1      8571512101                                      Weekly review   
2      8571511956  Chinese Cars Account For 76% Global EV and PHE...   
3      8571511074  TESLA I Its not only EV Cars. Elon Musk predic...   
4      8571511614  UK train passengers face "further misery" as f...   
..            ...                                                ...   
348  eng-10368906  BP to slash renewables investment and ramp up ...   
349  eng-10360298  "Remove Trade Tariffs for Nigeria": FG appeals...   
350  eng-10354241  Clean energy contributed 10% to China's GDP in...   
351  eng-10327507  Data science and AI: The twin engines powering...   
352  eng-10320057  Trump Suspends $5 Billion Electric Vehicle Cha...   

                                                  body     type  \
0    Electrical retailer Currys have scrapped advic...  article   
1    Education publisher Pearson on Friday said ann...  article   
2    Electric carsare demonstrating more market pen...  article   
3    This is not a short-term trade as you know fro...  article   
4    (Alliance News) - Train fares in England and W...  article   
..                                                 ...      ...   
348  Some shareholders and environmental groups hav...    event   
349  CHECK OUT: Education is Your Right! Don't Let ...    event   
350  Study found electric vehicles and batteries ad...    event   
351  Climate change faces its critical juncture tod...    event   
352  President Donald Trump's administration halted...    event   

                                                   txt  \
0    Currys scraps advice telling customers use a s...   
1    Weekly review. Education publisher Pearson on ...   
2    Chinese Cars Account For 76% Global EV and PHE...   
3    TESLA I Its not only EV Cars. Elon Musk predic...   
4    UK train passengers face "further misery" as f...   
..                                                 ...   
348  BP to slash renewables investment and ramp up ...   
349  "Remove Trade Tariffs for Nigeria": FG appeals...   
350  Clean energy contributed 10% to China's GDP in...   
351  Data science and AI: The twin engines powering...   
352  Trump Suspends $5 Billion Electric Vehicle Cha...   

                                          response_llm  
0    [{'word': 'Currys', 'entity': 'Brand'}, {'word...  
1    [{'word': 'Pearson', 'entity': 'Organization'}...  
2    [{'word': 'Chinese', 'entity': 'Country'}, {'w...  
3    [{'word': 'Tesla', 'entity': 'Brand'}, {'word'...  
4    [{'word': 'UK', 'entity': 'Country'}, {'word':...  
..                                                 ...  
348  [{'word': 'BP', 'entity': 'Organization'}, {'w...  
349  [{'word': 'Nigeria', 'entity': 'Country'}, {'w...  
350  [{'word': 'China', 'entity': 'Country'}, {'wor...  
351  [{'word': 'International Energy Agency', 'enti...  
352  [{'word': 'Trump', 'entity': 'Person'}, {'word...  

[353 rows x 6 columns]

In [ ]:
# Explode the list into multiple rows
df_exploded = data_news_use.explode('response_llm')

# Normalize the dictionary column into separate columns
df_entities = pd.json_normalize(df_exploded['response_llm'])

# Concatenate with 'uri' column
df_final = pd.concat([df_exploded[['uri','type']].reset_index(drop=True), df_entities], axis=1)

# Rename columns for clarity
df_final.rename(columns={'word': 'word', 'entity': 'entity'}, inplace=True)
df_final

uri     type                                      word  \
0       8571515568  article                                    Currys   
1       8571515568  article                                MailOnline   
2       8571515568  article                            Jessica Watson   
3       8571515568  article                                   Gloriah   
4       8571515568  article                             Holly Jackson   
...            ...      ...                                       ...   
5063  eng-10320057    event                              Donald Trump   
5064  eng-10320057    event                                     Biden   
5065  eng-10320057    event                              Emily Biondi   
5066  eng-10320057    event  National Electric Vehicle Infrastructure   
5067  eng-10320057    event              Department of Transportation   

                entity  
0                Brand  
1         Organization  
2               Person  
3                Brand  
4               Person  
...                ...  
5063            Person  
5064            Person  
5065            Person  
5066  Electric Vehicle  
5067      Organization  

[5068 rows x 4 columns]

In [ ]:
df_final.to_parquet("Data_use//unjoined_parquet//articles-events-entity.parquet")

In [ ]:
data_entity = df_final

In [ ]:
data_entity = pd.read_parquet("Data_use//unjoined_parquet//articles-events-entity.parquet")

In [ ]:
data_ent_country = df_final[df_final['entity']=='Country'].drop_duplicates(subset="word")
data_ent_country

uri     type            word   entity
57      8571512101  article    South Africa  Country
59      8571512101  article              UK  Country
67      8571512101  article              US  Country
69      8571512101  article         Germany  Country
71      8571512101  article          France  Country
...            ...      ...             ...      ...
4368    8574199196  article              SA  Country
4384    8574184065  article  Czech Republic  Country
4499    8574193273  article      Kazakhstan  Country
4834  eng-10384176    event      New Mexico  Country
4925  eng-10294659    event       Americans  Country

[135 rows x 4 columns]

In [ ]:
data_country = pd.read_parquet("Data_use\Europe_country.parquet")
data_country

country_name
0                   Albania
12                  Andorra
19              Netherlands
31                  Austria
40                  Belarus
47                  Belgium
50   Bosnia and Herzegovina
53                   Norway
64                   France
77                 Bulgaria
105                 Croatia
126          Czech Republic
140                 Denmark
145                 Estonia
160                 Finland
179                 Germany
195                  Greece
203                 Hungary
222                 Iceland
230                 Ireland
234              Kazakhstan
236                  Kosovo
243                  Serbia
268                   Italy
273                  Latvia
316           Liechtenstein
327               Lithuania
337              Luxembourg
349                  Monaco
350              Montenegro
373         North Macedonia
381                   Malta
449                 Moldova
486                  Poland
502                 Romania
544                  Russia
601              San Marino
610                Slovakia
618                Slovenia
620                   Spain
636                  Sweden
657             Switzerland
683            Vatican City
684                 Ukraine
711                  Turkey
716                 England
717                   Wales
722                Scotland
740        Northern Ireland
900                Portugal

In [ ]:
data_country.sort_values(by='country_name')

country_name
0                   Albania
12                  Andorra
31                  Austria
40                  Belarus
47                  Belgium
50   Bosnia and Herzegovina
77                 Bulgaria
105                 Croatia
126          Czech Republic
140                 Denmark
716                 England
145                 Estonia
160                 Finland
64                   France
179                 Germany
195                  Greece
203                 Hungary
222                 Iceland
230                 Ireland
268                   Italy
234              Kazakhstan
236                  Kosovo
273                  Latvia
316           Liechtenstein
327               Lithuania
337              Luxembourg
381                   Malta
449                 Moldova
349                  Monaco
350              Montenegro
19              Netherlands
373         North Macedonia
740        Northern Ireland
53                   Norway
486                  Poland
900                Portugal
502                 Romania
544                  Russia
601              San Marino
722                Scotland
243                  Serbia
610                Slovakia
618                Slovenia
620                   Spain
636                  Sweden
657             Switzerland
711                  Turkey
684                 Ukraine
683            Vatican City
717                   Wales

In [ ]:
data_join = pd.merge(data_ent_country, data_country, how='left', left_on='word', right_on='country_name')
data_join

uri     type            word   entity    country_name
0      8571512101  article    South Africa  Country             NaN
1      8571512101  article              UK  Country             NaN
2      8571512101  article              US  Country             NaN
3      8571512101  article         Germany  Country         Germany
4      8571512101  article          France  Country          France
..            ...      ...             ...      ...             ...
130    8574199196  article              SA  Country             NaN
131    8574184065  article  Czech Republic  Country  Czech Republic
132    8574193273  article      Kazakhstan  Country      Kazakhstan
133  eng-10384176    event      New Mexico  Country             NaN
134  eng-10294659    event       Americans  Country             NaN

[135 rows x 5 columns]

In [ ]:
data_ent_country_join = pd.merge(data_entity, data_join[['word','country_name']], how='left', left_on='word', right_on='word')
data_ent_country_join

uri     type                                      word  \
0       8571515568  article                                    Currys   
1       8571515568  article                                MailOnline   
2       8571515568  article                            Jessica Watson   
3       8571515568  article                                   Gloriah   
4       8571515568  article                             Holly Jackson   
...            ...      ...                                       ...   
5063  eng-10320057    event                              Donald Trump   
5064  eng-10320057    event                                     Biden   
5065  eng-10320057    event                              Emily Biondi   
5066  eng-10320057    event  National Electric Vehicle Infrastructure   
5067  eng-10320057    event              Department of Transportation   

                entity country_name  
0                Brand          NaN  
1         Organization          NaN  
2               Person          NaN  
3                Brand          NaN  
4               Person          NaN  
...                ...          ...  
5063            Person          NaN  
5064            Person          NaN  
5065            Person          NaN  
5066  Electric Vehicle          NaN  
5067      Organization          NaN  

[5068 rows x 5 columns]

In [ ]:
data_ent_loc = df_final[df_final['entity']=='Location'].drop_duplicates(subset="word")
data_ent_loc

uri     type              word    entity
54      8571512101  article       White House  Location
61      8571512101  article           Gatwick  Location
62      8571512101  article          Heathrow  Location
65      8571512101  article  House of Commons  Location
66      8571512101  article        Washington  Location
...            ...      ...               ...       ...
4892  eng-10301296    event         Minnesota  Location
4978  eng-10314835    event           KARACHI  Location
4983  eng-10314835    event           Karachi  Location
5017  eng-10326138    event          CHEYENNE  Location
5018  eng-10326138    event              Wyo.  Location

[473 rows x 4 columns]

In [ ]:
data_city = pd.read_parquet("Data_use\Europe_city_polygon.parquet")
data_city

name country_name  \
0               Berat      Albania   
1               Dibër      Albania   
2              Durrës      Albania   
3             Elbasan      Albania   
4                Fier      Albania   
..                ...          ...   
915         SANTARÃM     Portugal   
916          SETÃBAL     Portugal   
917  VIANA DO CASTELO     Portugal   
918         VILA REAL     Portugal   
919             VISEU     Portugal   

                                          geometry_str  
0    MULTIPOLYGON (((20.307643 40.708634, 20.379912...  
1    MULTIPOLYGON (((20.546079 41.821152, 20.513945...  
2    MULTIPOLYGON (((19.824312 41.568173, 19.904853...  
3    MULTIPOLYGON (((20.307643 40.708634, 20.117936...  
4    MULTIPOLYGON (((19.828649 40.867966, 19.737453...  
..                                                 ...  
915  MULTIPOLYGON (((-8.285089 39.79576, -8.284929 ...  
916  MULTIPOLYGON (((-8.88519 37.963108, -8.884859 ...  
917  MULTIPOLYGON (((-8.165043 41.817899, -8.165969...  
918  MULTIPOLYGON (((-7.974168 41.375196, -7.97355 ...  
919  MULTIPOLYGON (((-8.356217 40.367232, -8.356978...  

[920 rows x 3 columns]

In [ ]:
data_join_loc = pd.merge(data_ent_loc, data_city[['name','country_name']], how='left', left_on='word', right_on='name')
data_join_loc

uri     type              word    entity name country_name
0      8571512101  article       White House  Location  NaN          NaN
1      8571512101  article           Gatwick  Location  NaN          NaN
2      8571512101  article          Heathrow  Location  NaN          NaN
3      8571512101  article  House of Commons  Location  NaN          NaN
4      8571512101  article        Washington  Location  NaN          NaN
..            ...      ...               ...       ...  ...          ...
468  eng-10301296    event         Minnesota  Location  NaN          NaN
469  eng-10314835    event           KARACHI  Location  NaN          NaN
470  eng-10314835    event           Karachi  Location  NaN          NaN
471  eng-10326138    event          CHEYENNE  Location  NaN          NaN
472  eng-10326138    event              Wyo.  Location  NaN          NaN

[473 rows x 6 columns]

In [ ]:
data_ent_country_city_join = pd.merge(data_ent_country_join, data_join_loc[['word','name','country_name']], how='left', left_on='word', right_on='word')
data_ent_country_city_join

uri     type                                      word  \
0       8571515568  article                                    Currys   
1       8571515568  article                                MailOnline   
2       8571515568  article                            Jessica Watson   
3       8571515568  article                                   Gloriah   
4       8571515568  article                             Holly Jackson   
...            ...      ...                                       ...   
5063  eng-10320057    event                              Donald Trump   
5064  eng-10320057    event                                     Biden   
5065  eng-10320057    event                              Emily Biondi   
5066  eng-10320057    event  National Electric Vehicle Infrastructure   
5067  eng-10320057    event              Department of Transportation   

                entity country_name_x name country_name_y  
0                Brand            NaN  NaN            NaN  
1         Organization            NaN  NaN            NaN  
2               Person            NaN  NaN            NaN  
3                Brand            NaN  NaN            NaN  
4               Person            NaN  NaN            NaN  
...                ...            ...  ...            ...  
5063            Person            NaN  NaN            NaN  
5064            Person            NaN  NaN            NaN  
5065            Person            NaN  NaN            NaN  
5066  Electric Vehicle            NaN  NaN            NaN  
5067      Organization            NaN  NaN            NaN  

[5068 rows x 7 columns]

In [ ]:
# Fill missing country names in df1 using the country from df2 (merged_df['country_name_y'])
data_ent_country_city_join['country_name_x'].fillna(data_ent_country_city_join['country_name_y'], inplace=True)

# Drop the extra columns from the merge
data_ent_country_city_join_final = data_ent_country_city_join.loc[:, data_ent_country_city_join.columns != 'country_name_y']  # Keep only the necessary columns

# Rename the 'country_name_x' column to 'country'
data_ent_country_city_join_final.rename(columns={'country_name_x': 'country_name'}, inplace=True)
data_ent_country_city_join_final

C:\Users\user\AppData\Local\Temp\ipykernel_15352\3533488689.py:2: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  data_ent_country_city_join['country_name_x'].fillna(data_ent_country_city_join['country_name_y'], inplace=True)
C:\Users\user\AppData\Local\Temp\ipykernel_15352\3533488689.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_ent_

uri     type                                      word  \
0       8571515568  article                                    Currys   
1       8571515568  article                                MailOnline   
2       8571515568  article                            Jessica Watson   
3       8571515568  article                                   Gloriah   
4       8571515568  article                             Holly Jackson   
...            ...      ...                                       ...   
5063  eng-10320057    event                              Donald Trump   
5064  eng-10320057    event                                     Biden   
5065  eng-10320057    event                              Emily Biondi   
5066  eng-10320057    event  National Electric Vehicle Infrastructure   
5067  eng-10320057    event              Department of Transportation   

                entity country_name name  
0                Brand          NaN  NaN  
1         Organization          NaN  NaN  
2               Person          NaN  NaN  
3                Brand          NaN  NaN  
4               Person          NaN  NaN  
...                ...          ...  ...  
5063            Person          NaN  NaN  
5064            Person          NaN  NaN  
5065            Person          NaN  NaN  
5066  Electric Vehicle          NaN  NaN  
5067      Organization          NaN  NaN  

[5068 rows x 6 columns]

In [ ]:
data_ent_country_city_join_final.to_parquet("Data_use//joined_parquet//articles-events-entity-city-country.parquet")